# Object counter, using YOLOv8 y opencv. Counting with YOLOv8 simplified

Docs:
-   https://docs.ultralytics.com/es/guides/object-counting/#real-world-applications
-   https://github.com/python-dontrepeatyourself/Real-Time-Vehicle-Detection-Tracking-and-Counting-in-Python/tree/main
-   object_counter.py from ultralytics 
-   https://docs.ultralytics.com/es/reference/engine/results/#ultralytics.engine.results.Boxes.__init__


In [24]:
import cv2
from ultralytics import YOLO

class ObjectCounter:
    """With selected line start-end and color draws line and counts objects touching it
    """
    def __init__(self,line_start, line_end, color=(255,255,0),drawTracks=False) -> None:
        self.line_start = line_start
        self.line_end = line_end
        self.counter = 0
        self.color = color
        self.idsDict = {}
        self.drawTracks=drawTracks
      
     
    def countDetections(self, tracks,frame,classesNames=[2]):   
        """Extracts and processes tracks for object counting in a video stream.

        Args:
            tracks (List[ultralytics.engine.results.Results]): A list of tracking results, encapsulated in the Results class.
            frame (_type_):video frame
        """
        
        #We get from each of the detections, its id and centroid
        for box in tracks[0].boxes:
            x,y,w,h= box.xywh[0]
            id = int(box.id)
            
            print(box)
            
            #If the object class id is inside the class list ids then it counts it
            if box.cls in classesNames:

                #Then we see if it touches the line
                if y > self.line_start[1] and self.line_start[0] < x < self.line_end[0]:
                    #And if it is already inside the dictionary
                    if id not in self.idsDict:
                        self.counter += 1
                        self.idsDict[id] = True
                
                
                  
        #Drawing line and counter
        cv2.line(frame,self.line_start,self.line_end,self.color,2)
        cv2.putText(frame, f"{self.counter}",(self.line_start[0],self.line_start[1]),cv2.FONT_HERSHEY_DUPLEX,2,self.color,3)
                    

In [28]:
model = YOLO("yolov8s.pt")
cap = cv2.VideoCapture("trafficCam.mp4")
assert cap.isOpened(), "Error reading video file"

#Lines xy
start_line_A = (20, 480)
end_line_A = (480, 480)
start_line_B = (525, 480)
end_line_B = (745, 480)
start_line_C = (895, 480)
end_line_C = (1165, 480)

# Init Object Counter
counter = ObjectCounter(start_line_A,end_line_A)
counter2 = ObjectCounter(start_line_B,end_line_B,(255,0,255))
counter3 = ObjectCounter(start_line_C,end_line_C,(0,255,0))

while cap.isOpened():
    success, frame = cap.read()
    if not success:
        print("Video frame is empty or video processing has been successfully completed.")
        break
    
    #Track with yolo
    tracks = model.track(frame,persist=True, show=False)
    
    #We pass the frame with detections to the counters
    #annotated_frame = tracks[0].plot()
    counter.countDetections(tracks, frame)
    counter2.countDetections(tracks, frame)
    counter3.countDetections(tracks, frame)

    cv2.imshow('Objects counter',tracks[0].plot())
    if cv2.waitKey(1) == 27:
        break



cap.release()

cv2.destroyAllWindows()

print(f"Counter1: {counter.counter} //Counter12 {counter2.counter} //Counter3: {counter3.counter}")


0: 384x640 6 cars, 73.0ms
Speed: 1.0ms preprocess, 73.0ms inference, 0.0ms postprocess per image at shape (1, 3, 384, 640)
ultralytics.engine.results.Boxes object with attributes:

cls: tensor([2.])
conf: tensor([0.8746])
data: tensor([[225.8167, 275.4692, 318.5217, 361.5508,   1.0000,   0.8746,   2.0000]])
id: tensor([1.])
is_track: True
orig_shape: (720, 1280)
shape: torch.Size([1, 7])
xywh: tensor([[272.1692, 318.5100,  92.7050,  86.0815]])
xywhn: tensor([[0.2126, 0.4424, 0.0724, 0.1196]])
xyxy: tensor([[225.8167, 275.4692, 318.5217, 361.5508]])
xyxyn: tensor([[0.1764, 0.3826, 0.2488, 0.5022]])
ultralytics.engine.results.Boxes object with attributes:

cls: tensor([2.])
conf: tensor([0.8442])
data: tensor([[593.4576, 286.0091, 676.3537, 400.9533,   2.0000,   0.8442,   2.0000]])
id: tensor([2.])
is_track: True
orig_shape: (720, 1280)
shape: torch.Size([1, 7])
xywh: tensor([[634.9056, 343.4812,  82.8961, 114.9442]])
xywhn: tensor([[0.4960, 0.4771, 0.0648, 0.1596]])
xyxy: tensor([[593.